In [1]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
%matplotlib notebook

# Line Search

In [ ]:
# Example function and its gradient
def fun(x):
    return 0.01*x**2*np.cos(x)
def grad(x):
    return 0.02*x*np.cos(x) - 0.01*x**2*np.sin(x)

# phi and gradient of phi
def phi(x, p):
    def g(alpha):
        return fun(x + alpha*p)
    return g 
def phi_grad(x, p):
    def g(alpha):
        return -grad(x + alpha*p)**2
    return g

# sufficient decrease condition
def wolfe1(x, p, c1):
    g = phi(x, p)
    def h(alpha):
        return g(alpha) <= g(0) + c1*alpha*grad(x)*p
    return h 

# curvature condition
def wolfe2(x, p, c2):
    g = phi_grad(x, p)
    def h(alpha):
        return g(alpha)*p >= c2*grad(x)*p
    return h

# backtracking algorithm
def backtracking(x, p, c1, c2, rho, alpha, alpha1):
    alphas = [alpha]
    while not wolfe1(x, p, c1)(alpha):
        alpha = rho*alpha
        alphas.append(alpha)
    return alpha, alphas

# two-way backtracking
def twoway_backtracking(x, p, c1, c2, rho, alpha, alpha1):
    alphas = [alpha]
    if wolfe1(x, p, c1)(alpha):
        while wolfe1(x, p, c1)(alpha) and alpha <= 1:
            alpha = alpha/rho
            alphas.append(alpha)
        return alpha, alphas
    return backtracking(x, p, c1, c2, rho, alpha, alpha1)

# quadratic and cubic interpolation
def interpolate(x, p, c1, c2, rho, alpha0, alpha1):
    alphas = [alpha0]
    alpha1 = None
    alpha2 = None
    while not wolfe1(x, p, c1)(alpha0):
        if alpha1 is None:
            alpha1 = -phi_grad(x, p)(0)*alpha0**2/2*(phi(x,p)(alpha0) - phi(x,p)(0) - phi_grad(x,p)(alpha0))
            alphas.append(alpha1)
        else:
            d1 = phi_grad(x,p)(alpha0) + phi_grad(x,p)(alpha1) - 3*(phi(x,p)(alpha0) - phi(x,p)(alpha1))/(alpha0-alpha1)
            d2 = np.sqrt(d1**2 - phi_grad(x,p)(alpha0)*phi_grad(x,p)(alpha1))
            alpha2 = alpha1 - (alpha1 - alpha0)*(phi_grad(x,p)(alpha1) + d2 - d1)/(phi_grad(x,p)(alpha1) - phi_grad(x,p)(alpha0) + 2*d2)
            alpha1, alpha0 = alpha2, alpha1
            alphas.append(alpha2)
        if alpha1 > 1:
            break
    return alpha0, alphas

# line search 
def linesearch(x, p, c1, c2, rho, alpha0, alpha1):
    first = True
    alphas = []
    while True:
        if not wolfe1(x, p, c1)(alpha1) or (phi(x, p)(alpha1) >= phi(x, p)(alpha0) and not first):
            return zoom(x, p, c1, c2, alpha0, alpha1, alphas)
        elif np.abs(phi_grad(x,p)(alpha1)) <= -c2*phi_grad(x,p)(0):
            return (alpha1, alphas)
        elif phi_grad(x,p)(alpha1) >= 0:
            return zoom(x, p, c1, c2, alpha1, alpha0, alphas)
        alpha0, alpha1 = alpha1, 2*alpha1
        first = False
        count = alphas.append(alpha1)
    return None

def zoom(x, p, c1, c2, alphaLo, alphaHi, alphas=[]):
    while True:
        alpha_j = alphaLo + 0.5*(alphaHi - alphaLo)
        alphas.append(alpha_j)
        if alphaLo > alphaHi:
            alphaLo, alphaHi = alphaHi, alphaLo
        elif np.abs(alphaLo - alphaHi) < 1e-9:
            return alphaLo, alphas
        elif not wolfe1(x, p, c1)(alpha_j) or phi(x,p)(alpha_j) >= phi(x,p)(alphaLo):
            alphaHi = alpha_j
        elif wolfe2(x, p, c2)(alpha_j):
            return (alpha_j, alphas)
        elif phi_grad(x,p)(alpha_j)*(alphaHi - alphaLo) >= 0:
            alphaLo = alpha_j 
            alphaHi = alphaLo
        else:
            alphaLo = alpha_j
    return None

In [ ]:
def plot_anim(search_fun, gen_a0, gen_a1, name):
    x = np.linspace(15, 65, 500)
    f = fun(x)
    c1 = 1e-4
    c2 = 0.1
    rho = 0.9
    xk = 20
    fk = fun(xk)
    
    fig, ax = plt.subplots()
    tot = 0
    ax.plot(x, f, linewidth=2)
    xk_ax = ax.plot(xk, fk, 'x', markersize=15)[0]
    as_ax = ax.plot(xk, fk, 'o', markersize=10)[0]
    
    xks_x = []
    xks_y = []
    as_x = []
    as_y = []
    ak = 1
    xk1 = xk
    pk1 = -grad(xk1)
    
    for i in range(30):
        fk = fun(xk)
        pk = -grad(xk)

        a0 = gen_a0(ak, xk, pk, xk1, pk1)
        a1 = gen_a1(ak, xk, pk, xk1, pk1)
        ak, alphas = search_fun(xk, pk, c1, c2, rho, a0, a1)
        tot += len(alphas)
        alphas = np.array(alphas)
        xks_x.append([xk, xk + ak*pk])
        xks_y.append([fk, fun(xk + ak*pk)])
        as_x.append(xk + alphas*pk)
        as_y.append(phi(xk, pk)(alphas))
        xk1 = xk
        pk1 = pk
        xk = xk + ak*pk
    
    def update(frame):
        xk_ax.set_xdata(xks_x[frame])
        xk_ax.set_ydata(xks_y[frame])
        as_ax.set_xdata(as_x[frame])
        as_ax.set_ydata(as_y[frame])
    
    ani = animation.FuncAnimation(fig=fig, func=update, frames=30, interval=300)
    
    print(tot, fk, xk)
    ani.save(f"../figs/{name}.gif")
    ani.save(f"../figs/{name}.mp4")

In [ ]:
def gen_a1(ak, xk, pk, xk1, pk1):
    return 1

plot_anim(backtracking, gen_a1, gen_a1, "backtrack")

In [ ]:
def gen_a1(ak, xk, pk, xk1, pk1):
    return ak

plot_anim(twoway_backtracking, gen_a1, gen_a1, "twoway-backtrack")

In [ ]:
def gen_a1(ak, xk, pk, xk1, pk1):
    return ak*grad(xk1)*pk1/(grad(xk)*pk)

plot_anim(interpolate, gen_a1, gen_a1, "interpolate")

In [ ]:
def gen_a0(ak, xk, pk, xk1, pk1):
    return 0
def gen_a1(ak, xk, pk, xk1, pk1):
    return ak*grad(xk1)*pk1/(grad(xk)*pk)

plot_anim(linesearch, gen_a0, gen_a1, "linesearch")

# Conjugated Gradients

In [ ]:
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
%matplotlib inline

def plot_func(A00, A01, A11):
    A = np.array([[A00, A01], [A01, A11]])
    b = np.array([0, 0])
    xmin = -1
    xmax = 1
    npoints = 200
    
    x1, x2 = np.meshgrid(np.linspace(xmin, xmax, npoints), np.linspace(xmin, xmax, npoints))
    z = A[0,0]*x1**2 + A[1,1]*x2**2 + A[0,1]*x1*x2 + A[1,0]*x1*x2 - b[0]*x1 - b[0]*x2
    contours = plt.contour(x1,x2,z, colors='black')
    plt.clabel(contours, inline=True, fontsize=8)

#plt.savefig("test.png")
interact(plot_func, A00 = widgets.FloatText(
    value=1,
    description='A(0,0):',
    disabled=False
),A01 = widgets.FloatText(
    value=0,
    description='A(0,1), A(1,0):',
    disabled=False
),A11 = widgets.FloatText(
    value=1,
    description='A(1,1):',
    disabled=False
))

In [ ]:
fig, ax = plt.subplots()
plot_func(1, 0, 1)

A = np.array([[1,0],[0,1]])
b = np.array([0,0])
x = np.array([-0.7, -0.7])
ps = np.array([[1, 0], [0,1]])
fx = 0.5 * x.T @ A @ x - b.T @ x
i = 0
k = 0
ax.plot(x[0], x[1], '.', markersize=10, color='black')
ax.annotate(f'x{k}', (x[0], x[1]), size=15, color='black')

while fx != 0:
    k = k + 1
    dfx = A @ x - b
    ak = - dfx @ ps[i,:] / (ps[i,:].T @ A @ ps[i,:])
    xn = x + ak * ps[i,:]
    ax.plot(xn[0], xn[1], '.', markersize=10, color='black')
    ax.annotate(f'x{k}', (xn[0], xn[1]), size=15, color='black')
    ax.plot([x[0], xn[0]], [x[1],xn[1]], '--', linewidth=2, color = 'black')
    x = xn
    fx = 0.5 * x.T @ A @ x - b.T @ x
    i = 1 - i
plt.savefig("../figs/conjugated.png", bbox_inches="tight")

In [ ]:
fig, ax = plt.subplots()
plot_func(5, 2, 6)

A = np.array([[5,2],[2,6]])
b = np.array([0,0])
x = np.array([-0.7, -0.7])
ps = np.array([[1, 0], [0,1]])
fx = 0.5 * x.T @ A @ x - b.T @ x
i = 0
k = 0
ax.plot(x[0], x[1], '.', markersize=10, color='black')
ax.annotate(f'x{k}', (x[0], x[1]), size=15, color='black')
ms = 10
s = 15

while fx != 0:
    k = k + 1
    dfx = A @ x - b
    ak = - dfx @ ps[i,:] / (ps[i,:].T @ A @ ps[i,:])
    xn = x + ak * ps[i,:]
    ax.plot(xn[0], xn[1], '.', markersize=ms, color='black')
    ax.annotate(f'x{k}', (xn[0], xn[1]), size=s, color='black')
    ax.plot([x[0], xn[0]], [x[1],xn[1]], '--', linewidth=2, color = 'black')
    x = xn
    fx = 0.5 * x.T @ A @ x - b.T @ x
    i = 1 - i
    s -= 2
    ms -= 2
plt.savefig("../figs/notconjugated.png", bbox_inches="tight")

# Nonlinear Optimization

In [56]:
# Example function and its gradient
def fun(x):
    return (x[0]*x[1]*np.sin(x[2]) + np.exp(x[0]*x[1]))/x[2]
def grad(x):
    dfdx0 = (x[1]*np.sin(x[2]) + x[1]*np.exp(x[0]*x[1]))/x[2]
    dfdx1 = (x[0]*np.sin(x[2]) + x[0]*np.exp(x[0]*x[1]))/x[2]
    dfdx2 = -(np.exp(x[0]*x[1]) - x[0]*x[1]*x[2]*np.cos(x[2]) + x[0]*x[1]*np.sin(x[2]))/x[2]**2
    return np.array([dfdx0, dfdx1, dfdx2])
def hessdiag(x):
    d2x0 = x[1]*x[1]*np.exp(x[0]*x[1])/x[2]
    d2x1 = x[0]*x[0]*np.exp(x[0]*x[1])/x[2]
    d2x2 = 2*(x[0]*x[1]*np.sin(x[2]) + np.exp(x[0]*x[1]))/x[2]**3 - 2*x[0]*x[1]*np.cos(x[2])/x[2]**2 - x[0]*x[1]*np.sin(x[2])/x[2]
    return np.array([d2x0, d2x1, d2x2])
              
# phi and gradient of phi
def phi(x, p):
    def g(alpha):
        return fun(x + alpha*p)
    return g 
def phi_grad(x, p):
    def g(alpha):
        return np.dot(grad(x + alpha*p), p)
    return g

# sufficient decrease condition
def wolfe1(x, p, c1):
    g = phi(x, p)
    def h(alpha):
        return g(alpha) <= g(0) + c1*alpha* p.T @ grad(x)
    return h 

# curvature condition
def wolfe2(x, p, c2):
    g = phi_grad(x, p)
    def h(alpha):
        return np.abs(g(alpha)) <= -c2 * g(0)
    return h

# line search 
def linesearch(x, p, c1, c2, alpha0, alpha1):
    first = True
    alphas = []
    it = 0
    while it < 100:
        if not wolfe1(x, p, c1)(alpha1) or (phi(x, p)(alpha1) >= phi(x, p)(alpha0) and not first):
            return zoom(x, p, c1, c2, alpha0, alpha1, alphas)
        elif wolfe2(x, p, c2): 
            return (alpha1, alphas)
        elif phi_grad(x,p)(alpha1) >= 0:
            return zoom(x, p, c1, c2, alpha1, alpha0, alphas)
        alpha0, alpha1 = alpha1, 2*alpha1
        first = False
        count = alphas.append(alpha1)
        it += 1
    return (alpha1, alphas)

def zoom(x, p, c1, c2, alphaLo, alphaHi, alphas=[]):
    it = 0
    while it < 100:
        alpha_j = alphaLo + 0.5*(alphaHi - alphaLo)
        alphas.append(alpha_j)
        if alphaLo > alphaHi:
            alphaLo, alphaHi = alphaHi, alphaLo
        elif np.abs(alphaLo - alphaHi) < 1e-9:
            return alphaLo, alphas
        elif not wolfe1(x, p, c1)(alpha_j) or phi(x,p)(alpha_j) >= phi(x,p)(alphaLo):
            alphaHi = alpha_j
        elif wolfe2(x, p, c2)(alpha_j):
            return (alpha_j, alphas)
        elif phi_grad(x,p)(alpha_j)*(alphaHi - alphaLo) >= 0:
            alphaLo = alpha_j 
            alphaHi = alphaLo
        else:
            alphaLo = alpha_j
        it += 1
    return (alpha_j, alphas)

In [30]:
c1 = 0.01
c2 = 0.1

def almost0(v):
    return np.all(np.abs(v) <= 1e-6)

# polak
def polak_ribiere(xk, gradFk):
    ak = 1
    pk = -gradFk
    gradFk_prev = gradFk
    pk_prev = pk
    it = 0
    while not almost0(gradFk) and it < 1000:
        alpha = linesearch(xk, pk, c1, c2, 0, ak)[0]
        xk1 = xk + alpha * pk
        gradFk1 = grad(xk1)
        beta = max(0, np.dot(gradFk1, gradFk1-gradFk)/np.dot(gradFk, gradFk))
        pk1 = beta*pk - gradFk1
        gradFk_prev, gradFk = gradFk, gradFk1
        pk_prev, pk = pk, pk1
        ak = min(1, np.abs(2.02*(fun(xk) - fun(xk1))/(gradFk @ pk)))
        xk = xk1
        it += 1
    return xk

x0 = np.array([-2,1,1])
xopt = polak_ribiere(x0, grad(x0))
print(xopt, fun(xopt))

[-15.99410444  18.38141908   1.41210388] -205.57993610247664


In [36]:
def bfgs(xk, gradFk):
    I = np.identity(xk.shape[0])
    Hk = I
    it = 0
    while np.linalg.norm(gradFk) > 1e-6 and it < 1000:
        pk = - Hk @ gradFk
        alpha = linesearch(xk, pk, c1, c2, 0, 1)[0]
        if alpha == 0:
            break
        xk1 = xk + alpha * pk
        gradFk1 = grad(xk1)
        sk = xk1 - xk
        yk = gradFk1 - gradFk
        ys = yk.T @ sk
        Hk1 = (I - sk @ yk.T / ys) @ Hk @ (I - yk @ sk.T / ys) + (sk @ sk.T) / ys
        Hk = Hk1
        xk = xk1
        it += 1
    return xk
    
x0 = np.array([-2,1,1])
xopt = bfgs(x0, grad(x0))
print(xopt, fun(xopt))

[-5.36790896  6.42334745 -0.83849638] -30.579285148453703


# Differentiation

In [67]:
def findiff1(x, f, eps):
    e = np.identity(x.shape[0])
    return (f(x + eps*e) - f(x))/eps

def findiff2(x, f, eps):
    e = np.identity(x.shape[0])
    return (f(x + eps*e) - f(x - eps*e))/(2*eps)

def finhess1(x, f, eps):
    e = np.identity(x.shape[0])
    g1 = (f(x + 2*eps*e) - f(x + eps*e))/eps
    g2 = (f(x + eps*e) - f(x))/eps
    return (g1-g2)/eps

def finhess2(x, f, eps):
    e = np.identity(x.shape[0])
    g1 = (f(x + 2*eps*e) - f(x))/(2*eps)
    g2 = (f(x) - f(x - 2*eps*e))/(2*eps)
    return (g1-g2)/(2*eps)

In [75]:
x = np.array([1,1,1])

print("True grad: ", grad(x))
print("\t\t  Finite diff 1: \t\t\t Finite diff 2")

eps = 1e-1
while eps > 1e-10:
    print(f"eps = {eps:.2e}: ", findiff1(x, fun, eps), findiff2(x, fun, eps))
    eps /= 10

True grad:  [ 3.55975281  3.55975281 -3.01945051]
		  Finite diff 1: 			 Finite diff 2
eps = 1.00e-01:  [ 3.70031294  3.70031294 -2.78399006] [ 3.56428555  3.56428555 -3.04661284]
eps = 1.00e-02:  [ 3.57338964  3.57338964 -2.99372954] [ 3.55979812  3.55979812 -3.01971941]
eps = 1.00e-03:  [ 3.56111241  3.56111241 -3.01685448] [ 3.55975327  3.55975327 -3.0194532 ]
eps = 1.00e-04:  [ 3.55988873  3.55988873 -3.01919066] [ 3.55975282  3.55975282 -3.01945053]
eps = 1.00e-05:  [ 3.5597664   3.5597664  -3.01942452] [ 3.55975281  3.55975281 -3.01945051]
eps = 1.00e-06:  [ 3.55975417  3.55975417 -3.01944791] [ 3.55975281  3.55975281 -3.01945051]
eps = 1.00e-07:  [ 3.55975295  3.55975295 -3.01945025] [ 3.55975281  3.55975281 -3.01945051]
eps = 1.00e-08:  [ 3.55975285  3.55975285 -3.01945042] [ 3.55975283  3.55975283 -3.01945049]
eps = 1.00e-09:  [ 3.55975338  3.55975338 -3.01945047] [ 3.55975294  3.55975294 -3.01945069]
eps = 1.00e-10:  [ 3.55975693  3.55975693 -3.01944691] [ 3.55975249  3.55975

In [79]:
x = np.array([1,1,1])

print("True hessian: ", hessdiag(x))
print("\t\t  Finite diff 1:\t\t    Finite diff 2")

eps = 1e-1
while eps > 1e-10:
    print(f"eps = {eps:.2e}: ", finhess1(x, fun, eps), finhess2(x, fun, eps))
    eps /= 10

True hessian:  [2.71828183 2.71828183 5.19743003]
		  Finite diff 1:		    Finite diff 2
eps = 1.00e-01:  [3.00667033 3.00667033 3.89792931] [2.72735486 2.72735486 5.4243967 ]
eps = 1.00e-02:  [2.7456239  2.7456239  5.03983754] [2.71837244 2.71837244 5.19960996]
eps = 1.00e-03:  [2.7210017  2.7210017  5.18133549] [2.71828273 2.71828273 5.19745182]
eps = 1.00e-04:  [2.7185536  2.7185536  5.19581707] [2.71828186 2.71828186 5.19743025]
eps = 1.00e-05:  [2.7182967  2.7182967  5.19727372] [2.71828338 2.71828338 5.19743359]
eps = 1.00e-06:  [2.71871414 2.71871414 5.19628784] [2.7184921  2.7184921  5.19750909]
eps = 1.00e-07:  [2.62012634 2.62012634 5.2846616 ] [2.73114864 2.73114864 5.20694599]
eps = 1.00e-08:  [ 4.4408921  4.4408921 -8.8817842] [5.55111512 5.55111512 5.55111512]
eps = 1.00e-09:  [-888.1784197  -888.1784197   444.08920985] [111.02230246 111.02230246 222.04460493]
eps = 1.00e-10:  [-44408.92098501 -44408.92098501 -44408.92098501] [22204.4604925  22204.4604925  11102.23024625]
